In [6]:
from ndtools import staged_max_flow as smf

from pathlib import Path
import sys
import json

sys.path.insert(0, str(Path.cwd().parents[2]))
from tsum import tsum
import torch

In [12]:
import importlib
importlib.reload(tsum)

<module 'tsum.tsum' from 'c:\\Users\\jb622s\\git\\tsum\\tsum\\tsum.py'>

# Reliability analysis of benchmark gas supply plant

## Case 1: Original system

### Load data

In [33]:
DATASET = Path(r"data") 

nodes = json.loads((DATASET / "nodes.json").read_text(encoding="utf-8"))
edges = json.loads((DATASET / "edges.json").read_text(encoding="utf-8"))
probs_dict = json.loads((DATASET / "probs.json").read_text(encoding="utf-8"))


In [34]:
def s_fun(comps_st):
    flow, sys_st_str, min_comp_state = smf.sys_fun( comps_st, nodes, edges, probs_dict, target_flow = 0.5 )

    sys_st = 1 if sys_st_str == 's' else 0
    return flow, sys_st, min_comp_state

row_names = list(probs_dict.keys())
n_state = 2  # binary states: 0, 1

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
probs = [[probs_dict[n]['0']['p'], probs_dict[n]['1']['p']] for n in row_names]
probs = torch.tensor(probs, dtype=torch.float32, device=device)

### Get rules for system event

In [ ]:
sys_surv_st = 1 

result = tsum.run_rule_extraction_by_mcs(
    # Problem-specific callables / data
    sfun=s_fun,
    probs=probs,
    row_names=row_names,
    n_state=n_state,
    sys_surv_st=sys_surv_st,
    unk_prob_thres = 1e-6,
    output_dir="tsum_res"
) 

---
Round: 1, Unk. prob.: 1.000e+00
Surv probs: 0.000e+00, Fail probs: 0.000e+00
No. of non-dominant rules: 0, Survival rules: 0, Failure rules: 0
Survival sample found from sampling.
No. of existing rules removed:  0
New rule added. System state: 1, System value: 1.0. Total samples: 100000.
New rule (No. of conditions: 33): {'x1': ('>=', 1), 'x2': ('>=', 1), 'x24': ('>=', 1), 'x25': ('>=', 1), 'x26': ('>=', 1), 'x27': ('>=', 1), 'x28': ('>=', 1), 'x29': ('>=', 1), 'x30': ('>=', 1), 'x31': ('>=', 1), 'x32': ('>=', 1), 'x33': ('>=', 1), 'x35': ('>=', 1), 'x46': ('>=', 1), 'x61': ('>=', 1), 'x62': ('>=', 1), 'x64': ('>=', 1), 'x66': ('>=', 1), 'x68': ('>=', 1), 'x70': ('>=', 1), 'x73': ('>=', 1), 'x76': ('>=', 1), 'x77': ('>=', 1), 'x78': ('>=', 1), 'x79': ('>=', 1), 'x80': ('>=', 1), 'x81': ('>=', 1), 'x82': ('>=', 1), 'x83': ('>=', 1), 'x84': ('>=', 1), 'x85': ('>=', 1), 'x86': ('>=', 1), 'x87': ('>=', 1), 'sys': ('>=', 1)}
Updated sys_vals: [1.0]
---
Round: 2, Unk. prob.: 1.000e+00
Su

## Case 2: Addition Importance Measure

This measure quantifies the increase in system reliability when the same component is added to the system.

This can be computed by creating a duplicate of the component in the system structure, and evaluating the system reliability with the duplicated component working.

This measure is not officially included in the publication because it does not give additional insights compared to Birnbaum's measure.
Yet it is implemented here for demonstration purposes.

### Get rules for system event with each component added

In [ ]:
for x in probs_dict.keys():
    print(f"Adding component: {x}")

    new_nodes, new_edges, new_probs = smf.add_a_component(x, nodes, edges, probs_dict)
    def s_fun(comps_st):
        flow, sys_st_str, min_comp_state = smf.sys_fun( comps_st, new_nodes, new_edges, new_probs, target_flow = 0.5 )

        sys_st = 1 if sys_st_str == 's' else 0
        return flow, sys_st, None
    
    row_names = list(new_probs.keys())
    n_state = 2  # binary states: 0, 1
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    probs = [[new_probs[n]['0']['p'], new_probs[n]['1']['p']] for n in row_names]
    probs = torch.tensor(probs, dtype=torch.float32, device=device)

    # get rules
    sys_surv_st = 1
    
    result = tsum.run_rule_extraction_by_mcs(
        # Problem-specific callables / data
        sfun=s_fun,
        probs=probs,
        row_names=row_names,
        n_state=n_state,
        sys_surv_st=sys_surv_st,
        unk_prob_thres = 1e-5,
        output_dir=rf"tsum_res_aim/{x}"
    ) 

## Case 3: Deactivation Importance Measure

This measure quantifies the decrease in system reliability when the component is removed from the system.

This can be computed by removing the components, and evaluating the system reliability without the removed component.

This measure is not officially included in the publication because it does not give additional insights compared to Birnbaum's measure.
Yet it is implemented here for demonstration purposes.

### Get rules for system event with each component deactivated

In [ ]:
for x in probs_dict.keys():
    print(f"Deactivating component: {x}")

    new_nodes, new_edges, new_probs = smf.deactivate_a_component(x, nodes, edges, probs_dict)

    def s_fun(comps_st):
        flow, sys_st_str, min_comp_state = smf.sys_fun( comps_st, new_nodes, new_edges, new_probs, target_flow = 0.5 )

        sys_st = 1 if sys_st_str == 's' else 0
        return flow, sys_st, None
    
    row_names = list(new_probs.keys())
    n_state = 2  # binary states: 0, 1
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    probs = [[new_probs[n]['0']['p'], new_probs[n]['1']['p']] for n in row_names]
    probs = torch.tensor(probs, dtype=torch.float32, device=device)

    # get rules
    sys_surv_st = 1
    
    result = tsum.run_rule_extraction_by_mcs(
        # Problem-specific callables / data
        sfun=s_fun,
        probs=probs,
        row_names=row_names,
        n_state=n_state,
        sys_surv_st=sys_surv_st,
        unk_prob_thres = 1e-5,
        output_dir=rf"tsum_res_dim/{x}"
    ) 

Deactivating component: x1
---
Round: 1, Unk. prob.: 1.000e+00
Surv probs: 0.000e+00, Fail probs: 0.000e+00
No. of non-dominant rules: 0, Survival rules: 0, Failure rules: 0
Failure sample found from sampling.
No. of existing rules removed:  0
New rule added. System state: 0, System value: -0.0. Total samples: 100000.
New rule (No. of conditions: 1): {'x2': ('<=', 0), 'sys': ('<=', 0)}
Updated sys_vals: [0.0]
---
Round: 2, Unk. prob.: 1.000e+00
Surv probs: 0.000e+00, Fail probs: 0.000e+00
No. of non-dominant rules: 1, Survival rules: 0, Failure rules: 1
Survival sample found from sampling.
No. of existing rules removed:  0
New rule added. System state: 1, System value: 0.5. Total samples: 100000.
New rule (No. of conditions: 18): {'x2': ('>=', 1), 'x12': ('>=', 1), 'x13': ('>=', 1), 'x29': ('>=', 1), 'x30': ('>=', 1), 'x32': ('>=', 1), 'x33': ('>=', 1), 'x35': ('>=', 1), 'x46': ('>=', 1), 'x51': ('>=', 1), 'x53': ('>=', 1), 'x54': ('>=', 1), 'x55': ('>=', 1), 'x56': ('>=', 1), 'x61': (

# Case 4: Modified system

By adding the six most important components, and removing the six least, according to Birbaum's measure.

In [21]:
comps_to_add = ['x30', 'x33', 'x35', 'x46', 'x61', 'x87']
comps_to_remove = ['x22', 'x23', 'x24', 'x25', 'x26', 'x27']

Load data to find rules.

In [29]:
import copy

DATASET = Path(r"data") 

nodes = json.loads((DATASET / "nodes.json").read_text(encoding="utf-8"))
edges = json.loads((DATASET / "edges.json").read_text(encoding="utf-8"))
probs_dict = json.loads((DATASET / "probs.json").read_text(encoding="utf-8"))

new_nodes, new_edges, new_probs =copy.deepcopy(nodes), copy.deepcopy(edges), copy.deepcopy(probs_dict)
for x in comps_to_add:
    new_nodes, new_edges, new_probs = smf.add_a_component(x, new_nodes, new_edges, new_probs)
for x in comps_to_remove:
    new_nodes, new_edges, new_probs = smf.deactivate_a_component(x, new_nodes, new_edges, new_probs)

def s_fun(comps_st):
    flow, sys_st_str, min_comp_state = smf.sys_fun( comps_st, new_nodes, new_edges, new_probs, target_flow = 0.5 )

    sys_st = 1 if sys_st_str == 's' else 0
    return flow, sys_st, min_comp_state

row_names = list(new_probs.keys())
n_state = 2  # binary states: 0, 1
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
probs = [[new_probs[n]['0']['p'], new_probs[n]['1']['p']] for n in row_names]
probs = torch.tensor(probs, dtype=torch.float32, device=device)

In [32]:
sys_surv_st = 1 

result = tsum.run_rule_extraction_by_mcs(
    # Problem-specific callables / data
    sfun=s_fun,
    probs=probs,
    row_names=row_names,
    n_state=n_state,
    sys_surv_st=sys_surv_st,
    unk_prob_thres = 1e-6,
    output_dir="tsum_res_mod"
) 

---
Round: 1, Unk. prob.: 1.000e+00
Surv probs: 0.000e+00, Fail probs: 0.000e+00
No. of non-dominant rules: 0, Survival rules: 0, Failure rules: 0
Survival sample found from sampling.
No. of existing rules removed:  0
New rule added. System state: 1, System value: 0.5. Total samples: 100000.
New rule (No. of conditions: 20): {'x1': ('>=', 1), 'x7': ('>=', 1), 'x8': ('>=', 1), 'x29': ('>=', 1), 'x30': ('>=', 1), 'x31': ('>=', 1), 'x33': ('>=', 1), 'x36': ('>=', 1), 'x38': ('>=', 1), 'x40': ('>=', 1), 'x42': ('>=', 1), 'x43': ('>=', 1), 'x44': ('>=', 1), 'x45': ('>=', 1), 'x83': ('>=', 1), 'x86': ('>=', 1), 'x87': ('>=', 1), 'x35_copy': ('>=', 1), 'x46_copy': ('>=', 1), 'x61_copy': ('>=', 1), 'sys': ('>=', 1)}
Updated sys_vals: [0.5]
---
Round: 2, Unk. prob.: 1.000e+00
Surv probs: 0.000e+00, Fail probs: 0.000e+00
No. of non-dominant rules: 1, Survival rules: 1, Failure rules: 0
Survival sample found from sampling.
No. of existing rules removed:  0
New rule added. System state: 1, System 

KeyboardInterrupt: 